<a href="https://colab.research.google.com/github/himbeeer/ISOM-3360-PJ/blob/main/Tablet.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Import packages**

In [ ]:
from google.colab.widgets import TabBar
import ipywidgets as widgets
import time
import pandas as pd
from ipywidgets import interact, Text, DatePicker, IntText, Label, Layout, Button, Box, GridspecLayout, Checkbox, Output
from datetime import date

In [ ]:
# -- Install and setup Oracle Instant Client --
! wget -O oracleinstantclient.zip https://download.oracle.com/otn_software/linux/instantclient/19600/instantclient-basic-linux.x64-19.6.0.0.0dbru.zip
! unzip -oq oracleinstantclient.zip
! mkdir -p /opt/oracle
! mv instantclient_19_6 /opt/oracle/
! sh -c "echo /opt/oracle/instantclient_19_6 > /etc/ld.so.conf.d/oracle-instantclient.conf"
! ldconfig


# -- Include cx_Oracle package --
! pip install cx_Oracle


--2024-05-01 08:31:56--  https://download.oracle.com/otn_software/linux/instantclient/19600/instantclient-basic-linux.x64-19.6.0.0.0dbru.zip
Resolving download.oracle.com (download.oracle.com)... 23.62.176.91
Connecting to download.oracle.com (download.oracle.com)|23.62.176.91|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 75462547 (72M) [application/zip]
Saving to: ‘oracleinstantclient.zip’

oracleinstantclient 100%[===================>]  71.97M   133MB/s    in 0.5s    

2024-05-01 08:31:57 (133 MB/s) - ‘oracleinstantclient.zip’ saved [75462547/75462547]

/sbin/ldconfig.real: /usr/local/lib/libtbbbind_2_5.so.3 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbbbind.so.3 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbbbind_2_0.so.3 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbbmalloc.so.2 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbbmalloc_proxy.so.2 is not a symbolic link

/sbin/ldconf

In [ ]:
import cx_Oracle

HOST_NAME = "imz409.ust.hk"
PORT_NUMBER = "1521"
SERVICE_NAME = "imz409"
USERNAME = "LA202"
PASSWORD = "38NA"
dsn_tns = cx_Oracle.makedsn(HOST_NAME, PORT_NUMBER, service_name=SERVICE_NAME)
conn = cx_Oracle.connect(user=USERNAME, password=PASSWORD, dsn=dsn_tns)
c = conn.cursor()

# **Helper functions**

## check_password()

In [ ]:
def check_password(man_id: str, password: str) -> bool:
    # Convert man_id to string, in case it's not already
    man_id_str = str(man_id)

    # Check if man_id is not numeric, return False immediately
    if not man_id_str.isdigit():
        return False

    query = "SELECT man_pw FROM manager WHERE man_id = :man_id"
    c.execute(query, {'man_id': man_id_str})
    result = c.fetchone()  # This will fetch the first row returned by the query

    # Check if the query returned a result and if the password matches
    if result and result[0] == password:
        return True
    else:
        return False

## convert_to_bold()

In [ ]:
def convert_to_bold(text):
  '''
  Convert a string into sans bold.
  '''
  sans_bold_mapping = {
      'A': '𝗔', 'B': '𝗕', 'C': '𝗖', 'D': '𝗗', 'E': '𝗘', 'F': '𝗙', 'G': '𝗚', 'H': '𝗛', 'I': '𝗜', 'J': '𝗝',
      'K': '𝗞', 'L': '𝗟', 'M': '𝗠', 'N': '𝗡', 'O': '𝗢', 'P': '𝗣', 'Q': '𝗤', 'R': '𝗥', 'S': '𝗦', 'T': '𝗧',
      'U': '𝗨', 'V': '𝗩', 'W': '𝗪', 'X': '𝗫', 'Y': '𝗬', 'Z': '𝗭',
      'a': '𝗮', 'b': '𝗯', 'c': '𝗰', 'd': '𝗱', 'e': '𝗲', 'f': '𝗳', 'g': '𝗴', 'h': '𝗵', 'i': '𝗶', 'j': '𝗷',
      'k': '𝗸', 'l': '𝗹', 'm': '𝗺', 'n': '𝗻', 'o': '𝗼', 'p': '𝗽', 'q': '𝗾', 'r': '𝗿', 's': '𝘀', 't': '𝘁',
      'u': '𝘂', 'v': '𝘃', 'w': '𝘄', 'x': '𝘅', 'y': '𝘆', 'z': '𝘇',
      '0': '𝟬', '1': '𝟭', '2': '𝟮', '3': '𝟯', '4': '𝟰', '5': '𝟱', '6': '𝟲', '7': '𝟳', '8': '𝟴', '9': '𝟵'
  }

  sans_bold_text = ''

  for char in text:
      if char in sans_bold_mapping:
          sans_bold_text += sans_bold_mapping[char]
      else:
          sans_bold_text += char
  return sans_bold_text

convert_to_bold("Manage Accounts")

'𝗠𝗮𝗻𝗮𝗴𝗲 𝗔𝗰𝗰𝗼𝘂𝗻𝘁𝘀'

# **Global variables**
Modify/access these variables from within the functions of each screen.

In [ ]:
TAB_TA_ID = -1            # Current table ID
TAB_TR_ID = -1            # Current transaction ID

TABLE_CAPACITY = {}       # A dictionary for storing the table capacities

SHOPPING_CART = {}        # Stores the items inside the shopping cart

FOOD_INV = {}             # Stores the inventory of the available food items
FOOD_CAT = {}             # Stores the available food categories, and the corresponding sales volume
FOOD_ITEMS = []           # Stores the available food items
FOOD_ID_TO_NAME = {}      # Map each F_ID with the corresponding F_NAME

# Reset the available food inventory and categories after submitting an order
def reset_food_inv_cat(clear_cart):
  # Indicate whether the shopping cart is modified or not
  cart_modified = False

  global FOOD_ITEMS
  FOOD_ITEMS = c.execute('''
                          SELECT f.F_ID, F_INV, F_CAT, F_NAME, F_DESC, F_PRICE, SUM(CO_QTY)
                          FROM FOOD f LEFT OUTER JOIN COOKING_ORDER co
                          ON f.F_ID = co.FOOD_F_ID
                          WHERE F_AVAIL = 'Y'
                          AND F_INV > 0
                          GROUP BY f.F_ID, F_INV, F_CAT, F_NAME, F_DESC, F_PRICE
                          ORDER BY F_NAME''').fetchall()

  global FOOD_INV
  FOOD_INV = {}
  for food in FOOD_ITEMS:
    FOOD_INV[food[0]] = food[1]

  global FOOD_ID_TO_NAME
  FOOD_ID_TO_NAME = {}
  for food in FOOD_ITEMS:
    FOOD_ID_TO_NAME[food[0]] = food[3]

  global FOOD_CAT
  FOOD_CAT = {i[0]: (i[1] or 0) for i in c.execute('''SELECT F_CAT, SUM(CO_QTY)
                                                      FROM FOOD f LEFT OUTER JOIN COOKING_ORDER co
                                                      ON f.F_ID = co.FOOD_F_ID
                                                      WHERE F_AVAIL = 'Y'
                                                      AND F_INV > 0
                                                      GROUP BY F_CAT''').fetchall()}

  global SHOPPING_CART
  if clear_cart:
    SHOPPING_CART = {}
    cart_modified = True
  else:
    for key in dict(SHOPPING_CART).keys():
      # If the item in SHOPPING_CART is no longer available
      if key not in FOOD_INV.keys():
        SHOPPING_CART.pop(key)    # Remove the item from SHOPPING_CART
        cart_modified = True
      elif FOOD_INV[key] < SHOPPING_CART[key]:
        # If the food inventory is updated, and new inventory < quantity ordered
        SHOPPING_CART[key] = FOOD_INV[key]
        cart_modified = True

  return cart_modified


# Reset all global variables
def reset_global_variables():
  global TAB_TA_ID
  TAB_TA_ID = -1

  global TAB_TR_ID
  TAB_TR_ID = -1

  global TABLE_CAPACITY
  TABLE_CAPACITY = {i[0]: i[1] for i in c.execute("SELECT TA_ID, TA_CAP FROM TABLEE").fetchall()}

  reset_food_inv_cat(clear_cart=True)


# --------------------------------------------------------------------------------------------------------------------------

reset_global_variables()

print(TABLE_CAPACITY)
print(SHOPPING_CART)
print(FOOD_INV)
print(FOOD_CAT)
FOOD_ITEMS

{3: 4, 4: 4, 5: 5, 1: 3, 2: 2}
{}
{9: 4, 5: 4, 3: 11, 10: 3, 1: 10, 11: 14, 4: 7, 8: 36}
{'Main': 10, 'Side': 22, 'Drinks': 32}


[(9, 4, 'Drinks', 'Americano', 'Black coffee ##', 12.99, 8),
 (5,
  4,
  'Drinks',
  'Chicken Breast milkshake',
  'Blended meat soup L0L.',
  11.99,
  24),
 (3, 11, 'Main', 'Lasagna', 'Good Taste!', 12.55, 6),
 (10, 3, 'Main', 'Lucky Cake', 'Eat to feel lucky', 92.0, None),
 (1, 10, 'Main', 'Pineapple Pie ', 'Nothing Special.', 9.99, 3),
 (11,
  14,
  'Main',
  'Pizzzzzzzaaaaa',
  'the smelliest pizza in the world',
  2.0,
  1),
 (4, 7, 'Side', 'Salad', 'Just Salad.', 9.99, 22),
 (8,
  36,
  'Main',
  'Super Super Nice Bagel',
  'Perfect Circled Bagel',
  45.0,
  None)]

# **Upload images**

In [ ]:
instructionlabel = widgets.Label("Please upload \"foodImages.zip\"")
uploader = widgets.FileUpload(accept='.zip', multiple=False)
btnUpload = widgets.Button(description="OK")

def btnUpload_on_click(b):
    try:
        input_file = list(uploader.value.values())[0]
        if input_file['metadata']['name'] == 'foodImages.zip':
            with open(input_file['metadata']['name'], "wb") as fp:
                fp.write(input_file['content'])
            !unzip -o foodImages.zip
            # global foodImages_uploaded    # mark global so that changes in the next line is effective to the program
            # foodImages_uploaded = True
        else:
            b.description = "Retry"
    except:
        return
btnUpload.on_click(btnUpload_on_click)

foodImages_uploaded = False
display(widgets.HBox([instructionlabel, uploader, btnUpload]))

# **Tablet - Classes**

## SelectTable

In [ ]:
class SelectTable:
  select_table_grid = None
  table_number_btn = None
  headcount_dropdown = None
  login_btn = None
  username = None
  password = None

  def __init__(self):
    self.select_table_grid = GridspecLayout(8, 1, width = '800px',
                                            layout = widgets.Layout(justify_items = 'center'))
    self.select_table_number()
    self.login()
    display(self.select_table_grid)

  def get_available_tables(self):
    '''
    Helper function: get the tables currently available.
    '''
    query = "SELECT ta_id FROM tablee WHERE ta_status = 'Available' ORDER BY ta_id ASC"

    # Assuming 'c' is a valid cursor object
    c.execute(query)
    result = c.fetchall()  # This will fetch the first row returned by the query

    table_list = []
    for t in result:
      for id in t:
        table_list.append(id)

    if not table_list:
      table_list = ["No table available."]

    return table_list

  def select_table_number(self):
    # ----------------------------------------------------------------------------------------------------------------

    # Label: Available Tables
    table_number_label = Label(value = "𝗔𝘃𝗮𝗶𝗹𝗮𝗯𝗹𝗲 𝗧𝗮𝗯𝗹𝗲𝘀")

    # ----------------------------------------------------------------------------------------------------------------

    # Button: Table Number
    self.table_number_btn = widgets.ToggleButtons(
          options=self.get_available_tables())
    # ----------------------------------------------------------------------------------------------------------------

    # Dropdown: Headcount
    def on_table_number_btn_clicked(b):
      self.headcount_dropdown.options = get_headcount_options()
    self.table_number_btn.observe(on_table_number_btn_clicked, "value")

    def get_headcount_options():
      # Show empty dropdown when there's no table available
      if self.table_number_btn.value == "No table available.":
        return []

      global TABLE_CAPACITY
      # Check the table capacity from the global dictionary
      return list(range(1, TABLE_CAPACITY[self.table_number_btn.value] + 1))

    self.headcount_dropdown = widgets.Dropdown(options = get_headcount_options(), description='Headcount:')
    self.headcount_dropdown.layout.width = '150px'

    # ----------------------------------------------------------------------------------------------------------------

    # Button: Refresh Availability
    refresh_btn = Button(description = "Refresh Availability")
    def on_refresh_btn_clicked(b):
      table_list = self.get_available_tables()
      self.table_number_btn.options =  table_list
      if table_list == ["No table available."]:
        self.select_table_grid[7, :].disabled = True # Disable the "Login" button
      else:
        self.select_table_grid[7, :].disabled = False # Enable the "Login" button

    refresh_btn.on_click(on_refresh_btn_clicked)

    # ----------------------------------------------------------------------------------------------------------------

    # Display
    self.select_table_grid[0:3, :] = widgets.VBox([table_number_label, self.table_number_btn, self.headcount_dropdown, refresh_btn],
                                                  layout = widgets.Layout(justify_content='center', align_items='center'))

  def login(self):
      username_field = widgets.Text(description='Username:')
      password_field = widgets.Password(description='Password:')

      # ----------------------------------------------------------------------------------------------------------------

      # Button: Login
      self.login_button = widgets.Button(description='Login')

      def on_login_button_clicked(_):
          # Double check if the table is really available at this moment
          if self.table_number_btn.value not in self.get_available_tables():
            self.select_table_grid.close()
            SelectTable()
            return

          self.username = username_field.value
          self.password = password_field.value

          # Error handling
          is_password_correct = check_password(self.username, self.password)

          # If password is correct
          if is_password_correct:
            # Update the global variables
            global TAB_TA_ID
            TAB_TA_ID = self.table_number_btn.value

            # Calculate the ID of the new record
            max_query = "SELECT MAX(TR_ID) FROM TRANSACTION"
            c.execute(max_query)
            result = c.fetchone()[0]
            new_tr_id = (result or 0) + 1  # If there is no transaction record, result = None --> reset the value to 0

            global TAB_TR_ID
            TAB_TR_ID = new_tr_id   # Set global variable

            # INSERT INTO TRANSACTION
            insert_query = f'''INSERT INTO transaction (tr_id, tr_checkin, tr_status, tr_headcount, table_ta_id)
                               VALUES ({new_tr_id}, sysdate, 'Open', {self.headcount_dropdown.value}, {self.table_number_btn.value})'''
            # print(insert_query)
            c.execute(insert_query)
            conn.commit()

            # UPDATE TABLE (update the status)
            update_query = f"UPDATE tablee SET ta_status = 'Occupied' WHERE ta_id = {self.table_number_btn.value}"
            c.execute(update_query)
            conn.commit()

            # Close the screen
            self.select_table_grid.close()
            # Navigate to WelcomeScreen
            WelcomeScreen()

          else:
            self.select_table_grid[6,: ]=Label(value="Invalid username/password.")
          # -----------------------------------------------------

      self.login_button.on_click(on_login_button_clicked)

      # ----------------------------------------------------------------------------------------------------------------

      # Display
      self.select_table_grid[4:6, :] = widgets.VBox([username_field, password_field],
                                              layout = widgets.Layout(display='center', flex_flow='col', justify_content='center', align_items='center'))

      self.select_table_grid[7, :] = self.login_button
      # If there are no tables availabe --> disable the grid containing the login button
      if self.table_number_btn.value == "No table available.":
        self.select_table_grid[7, :].disabled = True

## WelcomeScreen

In [ ]:
class WelcomeScreen:
  welcome_grid = None

  def __init__(self):
    self.welcome_grid = GridspecLayout(2,2, grid_gap='0px', width='410px')
    # Label: Welcome to DB Cafe
    welcome_label = Label(value="𝗪𝗲𝗹𝗰𝗼𝗺𝗲 𝘁𝗼 𝗗𝗕 𝗖𝗮𝗳𝗲")
    self.welcome_grid[0,:] = widgets.HBox([welcome_label],
                                    layout = widgets.Layout(display='center', justify_content='center', align_items='center'))

# ----------------------------------------------------------------------------------------------------------------

    # Button: Enter Phone Number
    enter_phone_number_btn = widgets.Button(description="Enter Phone Number",
                                            layout = widgets.Layout(width='200px', height ='50px'))
    self.welcome_grid[1, 0] = enter_phone_number_btn

    def on_enter_phone_number_btn_clicked(b):
      # Close the welcome screen
      self.welcome_grid.close()
      # Navigate to RegisterPhoneNumber
      RegisterPhoneNumber()
    enter_phone_number_btn.on_click(on_enter_phone_number_btn_clicked)

# ----------------------------------------------------------------------------------------------------------------

    # Button: Order as Guest
    order_as_guest_btn = widgets.Button(description="Order as Guest",
                                        layout = widgets.Layout(width='200px', height='50px'))
    self.welcome_grid[1, 1] = order_as_guest_btn

    def on_order_as_guest_btn_clicked(b):
      # Close the welcome screen
      self.welcome_grid.close()
      # Navigate to OrderScreen
      MenuScreen()
    order_as_guest_btn.on_click(on_order_as_guest_btn_clicked)

# ----------------------------------------------------------------------------------------------------------------

    # Display the screen
    display(self.welcome_grid)

## RegisterPhoneNumber

In [ ]:
class RegisterPhoneNumber:
    def __init__(self):
        self.register_phone_grid = GridspecLayout(4, 1, grid_gap='0px', width='410px')

        # Label: Enter Phone Number
        enter_phone_label = Label(value="𝗘𝗻𝘁𝗲𝗿 𝗣𝗵𝗼𝗻𝗲 𝗡𝘂𝗺𝗯𝗲𝗿")
        self.register_phone_grid[0, :] = Box([enter_phone_label],
                                             layout=Layout(display='flex', justify_content='center', align_items='center'))

        # Textbox: Phone No:.
        self.phone_text = Text(description='Phone No:')
        self.register_phone_grid[1, :] = Box([self.phone_text],
                                             layout=Layout(display='flex', justify_content='center', align_items='center'))

        # Button: Login
        self.login_btn = Button(description="Login", layout=Layout(width='200px', height='30px'))
        self.register_phone_grid[3, :] = Box([self.login_btn],
                                             layout=Layout(display='flex', justify_content='center', align_items='center'))

        # Register the event handler for the login button
        self.login_btn.on_click(self.on_login_btn_clicked)

        # Display the screen
        display(self.register_phone_grid)

    def on_login_btn_clicked(self, b):
        # Error handling
        if len(self.phone_text.value) == 8 and self.phone_text.value.isdigit():
            # Assume TAB_TR_ID and other necessary variables are defined globally
            global TAB_TR_ID, c, conn
            # Valid phone number action here
            update_query = "UPDATE transaction SET tr_mobile = :mobile WHERE tr_id = :tr_id"
            c.execute(update_query, {'mobile': self.phone_text.value, 'tr_id': TAB_TR_ID})
            conn.commit()

            #Proceed to next screen or action
            self.register_phone_grid.close()  # Removed as .close() is not applicable
            MenuScreen()  # Navigate to MenuScreen or next action
          # print("Phone number registered successfully.")  # Placeholder action
        else:
            # Display error message for invalid phone number
            invalid_label = Label(value="Invalid phone number.")
            self.register_phone_grid[2, :] = Box([invalid_label],
                                                 layout=Layout(display='flex', justify_content='center', align_items='center'))

## MenuScreen

In [ ]:
class MenuScreen:
  menu_tabbar = None
  side_buttons = None

  def __init__(self):
    self.initialize_menu_tabbar()
    self.initialize_side_buttons()

  def showPage(self, tabName):
    with self.menu_tabbar.output_to(tabName):
      display()

  def initialize_menu_tabbar(self):
    # Update the available food inventory and shopping cart quantities
    reset_food_inv_cat(clear_cart=False)

    # Items on tabbar: "Top 5" + available food categories
    self.menu_tabbar = TabBar(["Top 5"] + list(FOOD_CAT.keys()), location = "top")

    retrieved_ids = []             # Keep track the ID of each food item. Used for "plus" and "minus" button
    retrieved_cats = []            # Keep track the category of each food item. Used for displaying each food item in the correct category tab
    retrieved_sales = []           # Keep track the sales volume of each food item. Used for sorting food items in "Top 5"

    food_item_gridlist = []        # 1 item in gridlist = 1 food item
    food_item_left_list = []       # Left component of each food item
    food_item_mid_list = []        # Middle component of each food item
    food_item_right_list = []      # Right component of each food item

    minus_btn_list = []            # Keep track for event handling
    plus_btn_list = []             # Keep track for event handling
    qty_label_list = []            # Keep track for event handling

    # Loop through every food item --> build one grid for each food item
    for food in FOOD_ITEMS:
      retrieved_ids.append(food[0])   # Record the retrieved IDs
      retrieved_cats.append(food[2])  # Record the retrieved categories
      retrieved_sales.append((food[6] or 0))

      # The LEFT content of each food item
      try:
        # Open the food image
        food_item_left = widgets.Image(value=open("foodImages/" + str(food[0]) + ".png", "rb").read(),
                                      format='png',
                                      width=110, height=110)
      except:
        # If the image cannot be found
        food_item_left = Label("No image found")
      # Build the LEFT list
      food_item_left_list.append(widgets.HBox([food_item_left],
                                              layout=widgets.Layout(align_items='center',
                                                                    justify_content='center')))

      # ----------------------------------------------------------------------------------------------
      # The MIDDLE content of each food item
      food_item_mid = GridspecLayout(4, 1, layout=widgets.Layout(max_height='115px'))

      food_item_mid[0, :] = Label(convert_to_bold(food[3]),
                                      layout = widgets.Layout(margin='0px'))
      food_item_mid[1, :] = Label(food[4],
                                      layout = widgets.Layout(margin='0px'))
      food_item_mid[2, :] = Label("$" + str(food[5]),
                                      layout = widgets.Layout(margin='0px'))
      food_item_mid[3, :] = Label("Sales volume: " + str(food[6] or 0),
                                      layout = widgets.Layout(margin='0px'))

      # Build the MIDDLE list
      food_item_mid_list.append(food_item_mid)

    # ----------------------------------------------------------------------------------------------

    # The RIGHT content of each food item
    minus_btn_list = [Button(description='-', layout = widgets.Layout(width='50px')) for i in range(len(retrieved_ids))]
    plus_btn_list = [Button(description='+', layout = widgets.Layout(width='50px')) for i in range(len(retrieved_ids))]
    qty_label_list = [Label(str(SHOPPING_CART.get(i, 0))) for i in retrieved_ids] # Retrieve the quantities in shopping cart

    # Button: Minus
    def on_minus_btn_clicked(b):
      button_num = 0
      for button_num in range(len(minus_btn_list)):
        if minus_btn_list[button_num] == b:          # button found
          id_selected = retrieved_ids[button_num]    # find the corresponding id
          label_selected = int(qty_label_list[button_num].value)

          # When current quantity in shopping cart >= 1 --> reduce ordered quantity by 1
          if label_selected >= 1:
            # Update the shopping cart
            SHOPPING_CART[id_selected] = SHOPPING_CART[id_selected]- 1
            # Update the qty label
            qty_label_list[button_num].value = str(SHOPPING_CART[id_selected])

          # If the updated quantity in shopping cart == 0 --> remove the food from the shopping cart
          if label_selected - 1 == 0:
            SHOPPING_CART.pop(id_selected)

          # Do not reduce the quantity when the ordered quantity is 0
          break
    for minus_btn in minus_btn_list:
      minus_btn.on_click(on_minus_btn_clicked)

    # Button: Plus
    def on_plus_btn_clicked(b):
      button_num = 0
      for button_num in range(len(plus_btn_list)):
        if plus_btn_list[button_num] == b:          # button found
          id_selected = retrieved_ids[button_num]   # find the corresponding id
          label_selected = int(qty_label_list[button_num].value)

          # If inventory can satisfy the new quantity --> add item to shopping cart
          if label_selected < FOOD_INV[id_selected]:
            # Update the shopping cart
            SHOPPING_CART[id_selected] = SHOPPING_CART.get(id_selected, 0) + 1
            # Update the qty label
            qty_label_list[button_num].value = str(SHOPPING_CART[id_selected])

          break

    for plus_btn in plus_btn_list:
      plus_btn.on_click(on_plus_btn_clicked)

    # Build the RIGHT list
    for i in range(len(retrieved_ids)):
      food_item_right_list.append(widgets.HBox([minus_btn_list[i], qty_label_list[i], plus_btn_list[i]],
                                  layout = widgets.Layout(align_items='center',
                                                          justify_content='center')))

    # ----------------------------------------------------------------------------------------------
    # Pack left, mid, right content into a single horizontal grid
    for left, mid, right in zip(food_item_left_list, food_item_mid_list, food_item_right_list):
      food_item_grid = GridspecLayout(1, 3, layout = widgets.Layout(border='1px solid grey',
                                                                    min_height='115px'))
      food_item_grid[:, 0] = left
      food_item_grid[:, 1] = mid
      food_item_grid[:, 2] = right
      food_item_gridlist.append(food_item_grid)

    # ----------------------------------------------------------------------------------------------

    # Display
    # Layout of the VBox of each tab
    box_layout = Layout(overflow='scroll',        # Scroll to the items that are out of boundary
                        border='1px solid black',
                        width='800px',
                        max_height='300px',
                        flex_flow='col',
                        display='flex')
    # Reference: https://ipywidgets.readthedocs.io/en/7.x/examples/Widget%20Styling.html?highlight=scroll


    # Loop through each food item
    # Display the food item in the corresponding category tab
    for category in FOOD_CAT.keys():
      with self.menu_tabbar.output_to(category, select=False):      # select=False to avoid jumping to each tab
        children_list = []
        # In the gridlist, add only the food items that match the category of the current tab
        for child_grid, child_category in zip(food_item_gridlist, retrieved_cats):
          if child_category == category:
            children_list.append(child_grid)

        # Display: Total category sales
        display(Label(f"Total sales volume of {category}: {FOOD_CAT[category]}"))
        # Display: food items
        display(widgets.VBox(children=children_list,
                            layout=box_layout))


    # Display in "Top 5"
    with self.menu_tabbar.output_to("Top 5", select=False):
      # Sort the grids based on the sales of each food item
      sortedGrids = sorted(zip(retrieved_sales, food_item_gridlist), key=lambda x: x[0], reverse=True)

      # Unpack into a list of sorted sales & a list of sorted grids
      _, sortedGrids = zip(*sortedGrids)

      # Display only the top 5 items in sortedGrids
      display(widgets.VBox(children=sortedGrids[:5],
                            layout=box_layout))

    # ----------------------------------------------------------------------------------------------------------
    self.showPage("Top 5")

  def initialize_side_buttons(self):

    # Button: View Cart
    view_cart_btn = Button(description = "View Cart")
    def on_view_cart_btn_clicked(b):
      self.menu_tabbar.remove()
      self.side_buttons.close()
      ShoppingCart()
    view_cart_btn.on_click(on_view_cart_btn_clicked)

    # -----------------------------------------------------------------------------------------------

    # Button: Ordered Items
    view_order_btn = Button(description = "Ordered Items")
    def on_view_order_btn_clicked(b):
      self.menu_tabbar.remove()
      self.side_buttons.close()
      OrderedItemsScreen()
    view_order_btn.on_click(on_view_order_btn_clicked)

    # -----------------------------------------------------------------------------------------------

    # Button: Checkout
    checkout_btn = widgets.Button(description="Checkout")
    def on_checkout_btn_clicked(b):
      self.menu_tabbar.remove()
      self.side_buttons.close()
      ResetTablet()
    checkout_btn.on_click(on_checkout_btn_clicked)

    # -----------------------------------------------------------------------------------------------

    # Button: Refresh Menu
    refresh_menu_btn = widgets.Button(description="Refresh Menu")
    def on_refresh_menu_btn_clicked(b):
      self.menu_tabbar.remove()
      self.side_buttons.close()
      self.initialize_menu_tabbar()
      self.initialize_side_buttons()
    refresh_menu_btn.on_click(on_refresh_menu_btn_clicked)

    self.side_buttons = widgets.HBox([view_cart_btn, view_order_btn, checkout_btn, refresh_menu_btn])
    display(self.side_buttons)

## r3

In [ ]:
#r3. Top 5 popular items by no. of sales, display also the no. of sales

class r3:
  top5_vbox = None

  def __init__(self):
    self.initialize_top5_report()

# Display List of Shopping Cart
  def initialize_top5_report(self):
      # Store the labels, hboxes of each row
      hboxes = []
      top5_labels = []

      # Insert table title into the first row of hboxes
      hboxes.insert(0, widgets.HBox([Label("Top 5 Items")]))

      # Insert table header into the second row of hboxes
      hboxes.insert(1, widgets.HBox([Label("ID", layout = widgets.Layout(width='80px')),
                                     Label("Name", layout = widgets.Layout(width='250px')),
                                     Label("Sales", layout = widgets.Layout(width='250px')),]))


      top5_query = '''SELECT F_ID, F_NAME, no_of_sales
                      FROM (
                          SELECT food.f_id, f_name, sum(co_qty) no_of_sales
                          FROM food INNER JOIN cooking_order
                          ON food.f_id = cooking_order.food_f_id
                          GROUP BY food.f_id, f_name
                          ORDER BY SUM(co_qty) DESC
                          )'''
      c.execute(top5_query)
      top5_results = c.fetchall()

      for i in top5_results[:5]:
        hboxes.append(widgets.HBox([Label(str(i[0]), layout = widgets.Layout(width='80px')),
                                    Label(str(i[1]), layout = widgets.Layout(width='250px')),
                                    Label(str(i[2]), layout = widgets.Layout(width='250px'))]))

      self.top5_vbox = widgets.VBox(hboxes)

      display(self.top5_vbox)

In [ ]:
ms = r3()

## r2

In [ ]:
from datetime import datetime, timedelta

hourly_revenue_grid = None

# Opening hours: 9:00am - 10:00pm
opening_hour = 9
closing_hour = 22

hourly_revenue_grid = GridspecLayout(closing_hour - opening_hour + 1, 8,
                                     layout=Layout(grid_gap='0px',
                                                   width='650px'))

# Label layout
label_layout = widgets.Layout(border = '1px solid grey', margin='0px', width='90px')

# Row/Column description
hourly_revenue_grid[0,0] = Label(convert_to_bold("Date/Time"), layout=label_layout)

# Row header: hour_py
row_grid_index = 1
for hour_py in range(opening_hour, closing_hour):
  label_layout = widgets.Layout(border = '1px solid grey', margin='0px', width='90px')
  hourly_revenue_grid[row_grid_index, 0] = Label(convert_to_bold(f"{hour_py}:00 - {hour_py}:59"),
                                                 layout=label_layout)
  row_grid_index += 1

# Retrieve hourly revenue from DB
sql_result = c.execute('''SELECT TO_CHAR(TR_CHECKIN, 'YYYY-MM-DD') TXN_Date,
                          TO_CHAR(TR_CHECKIN, 'HH24') Hours,
                          ROUND(SUM(TR_TOTAL * (1-TR_DISCOUNT_RATE)), 2) Total
                          FROM TRANSACTION
                          WHERE TO_CHAR(TR_CHECKIN, 'YYYY-MM-DD') >= TO_CHAR(SYSDATE-7, 'YYYY-MM-DD')
                          AND TO_CHAR(TR_CHECKIN, 'YYYY-MM-DD') < TO_CHAR(SYSDATE, 'YYYY-MM-DD')
                          GROUP BY TO_CHAR(TR_CHECKIN, 'YYYY-MM-DD'), TO_CHAR(TR_CHECKIN, 'HH24')
                          ORDER BY TO_CHAR(TR_CHECKIN, 'YYYY-MM-DD'), TO_CHAR(TR_CHECKIN, 'HH24')
                       ''').fetchall()

# If there are no sales in past 7 days --> replace sql_result with empty list
sql_result = sql_result or []

sql_row_index = 0                   # Row index of sql_result
col_grid_index = 1                  # Column index of grid

# List of the past 7 days
past_7_days = [(datetime.now() + timedelta(days=i)).strftime("%Y-%m-%d") for i in range(-7, 0)]

# Loop through each day
for date_py in past_7_days:
  label_layout = widgets.Layout(border = '1px solid grey',
                                margin='0px',
                                width='80px')
  # Column header: date_py
  hourly_revenue_grid[0, col_grid_index] = Label(convert_to_bold(date_py), layout=label_layout)

  # Set the row index to be processed
  row_grid_index = 1

  # Loop through each hour
  for hour_py in range(opening_hour, closing_hour):
    label_layout = widgets.Layout(border = '1px solid grey', margin='0px', width='80px')

    # Set initial cell value = 0
    hourly_revenue_grid[row_grid_index, col_grid_index] = Label('0', layout=label_layout)

    # If some rows in sql_result are not processed yet, check if we should update the value of the current grid cell
    if sql_row_index < len(sql_result):
      sql_row = sql_result[sql_row_index]

      # If sql_row record matches the grid cell that is currently processing
      if sql_row[0] == date_py and int(sql_row[1]) == hour_py:     # sql_row[1] = '09'
        # Write sales revenue in the grid cell
        hourly_revenue_grid[row_grid_index, col_grid_index] = Label(str(sql_row[2]), layout=label_layout)
        # Proceed to process next row in sql_result
        sql_row_index = sql_row_index+1

    # Move to next row
    row_grid_index += 1

  # Move to next column
  col_grid_index += 1

display(hourly_revenue_grid)

GridspecLayout(children=(Label(value='𝗗𝗮𝘁𝗲/𝗧𝗶𝗺𝗲', layout=Layout(border='1px solid grey', grid_area='widget001'…

## ShoppingCart

In [ ]:
# A global variable defined at the top of this ipynb file
FOOD_ID_TO_NAME = {9: 'Americano',
 5: 'Chicken Breast milkshake',
 3: 'Lasagna',
 1: 'Pineapple Pie ',
 4: 'Salad',
 8: 'Super Super Nice Bagel'}

In [ ]:
# So how to make use of FOOD_ID_TO_NAME?
FOOD_ID_TO_NAME[5]    # <-- use square bracket, and put the F_ID inside the square bracket

In [ ]:
# Assume there are some ordered items inside SHOPPING_CART already (added by MenuScreen already)
SHOPPING_CART = {4: 0, 9: 1, 5: 2}
SHOPPING_CART

In [ ]:
FOOD_ID_TO_NAME

In [ ]:
# How to get the values of SHOPPING_CART?
for f_id, f_qty in SHOPPING_CART.items():
  print(f_id, f_qty)

In [ ]:
class ShoppingCart:
  list_all_orders_vbox = None
  thank_you_vbox = None
  empty_vbox = None

  def __init__(self):
    self.initialize_list_shopping_cart()

  # Display List of Shopping Cart
  def initialize_list_shopping_cart(self, message=''):
      # Check if shopping cart is modified or not due to changes in food inventory/availability
      cart_modified = reset_food_inv_cat(clear_cart=False)
      if cart_modified:
        message = "One or more items in the shopping cart is modified due to changes in food inventory. Please check your order."

      # Store the labels, hboxes of each row
      id_labels = []
      name_labels = []
      qty_labels = []
      hboxes = []

      # Use a for loop to process each item in SHOPPING_CART
      for f_id, f_qty in SHOPPING_CART.items():
        # if f_qty is 0 --> use "continue" to skip this current loop, and go to the next item
        if f_qty == 0:
          continue

        # Maintain the list of F_IDs
        id_labels.append(f_id)

        # Maintain the label list of F_NAMEs (by querying the FOOD_ID_TO_NAME)
        name_labels.append(widgets.Label(value = str(FOOD_ID_TO_NAME[f_id]), layout = widgets.Layout(width='250px')))

        # Maintain the label list of quantity ordered (by querying the SHOPPIG_CART)
        qty_labels.append(widgets.Label(value = str(f_qty), layout = widgets.Layout(width='80px')))

        # -----------------------------------------------------------------------------------------------------------------------

      delete_buttons  = [widgets.Button(description="Delete") for i in range(len(id_labels))]

      # Button: Delete
      def on_delete_button_clicked(b):
          # check which button is being clicked
          button_num = 0
          for button_num in range(len(delete_buttons)):
            if delete_buttons[button_num] == b:   # button found!
              id_selected = id_labels[button_num]     # find the corresponding ID
              break

          # Remove the deleted food item from SHOPPING_CART
          SHOPPING_CART.pop(id_selected)
          # print(SHOPPING_CART)

          # Reload Shopping Cart
          self.list_shopping_cart_vbox.close()
          self.initialize_list_shopping_cart()

      for delete_button in delete_buttons:
          delete_button.on_click(on_delete_button_clicked)

      # Build the hboxes
      for i in range(len(id_labels)):
        hboxes.append(widgets.HBox([name_labels[i], qty_labels[i], delete_buttons[i]]))


      # Insert table header into the first row of hboxes
      hboxes.insert(0, widgets.HBox([Label("𝗡𝗮𝗺𝗲", layout = widgets.Layout(width='250px')),
                                      Label("𝗤𝘂𝗮𝗻𝘁𝗶𝘁𝘆", layout = widgets.Layout(width='80px'))]))

      hboxes.append(Label("_______________________________________________________________________________________"))

      # Label: show error message if SHOPPING_CART is modified upon submitting order
      if message != "":
        hboxes.append(Label(message))

      # Button: Back
      back_btn = widgets.Button(description="Back")
      def on_back_btn_clicked(b):
        self.list_shopping_cart_vbox.close()
        MenuScreen()
      back_btn.on_click(on_back_btn_clicked)

      # Button: Submit Order
      submit_btn = widgets.Button(description="Submit Order")

      hboxes.append(widgets.HBox([Label("", layout = widgets.Layout(width='0px')),
                                  back_btn,
                                  Label("", layout = widgets.Layout(width='180px')),
                                  submit_btn]))

      # When the button is clicked, go check what's inside SHOPPING_CART
      # And then insert the items one by one into the database
      # One row in your displayed table = one record in COOKING_ORDER
      def on_submit_button_clicked(b):
        # Check if the most updated food inventory/availability can satisfy the customer's order or not
        cart_modified = reset_food_inv_cat(clear_cart=False)
        if cart_modified:
          self.list_shopping_cart_vbox.close()
          self.initialize_list_shopping_cart(message = "One or more items in the shopping cart is modified due to changes in food inventory. Please check your order.")
          return

        for f_id, f_qty in SHOPPING_CART.items():
          if f_qty == 0:
            continue
          max_query = "SELECT MAX(CO_ID) FROM COOKING_ORDER"
          c.execute(max_query)
          result = c.fetchone()[0]
          new_co_id = (result or 0) + 1  # If there is no transaction record, result = None --> reset the value to 0

          #INSERT INTO COOKING ORDER
          insert_query = f'''INSERT INTO cooking_order (co_id, co_qty, co_status, co_sub_time, transaction_tr_id, food_f_id)
                             VALUES ({new_co_id}, {f_qty}, 'Preparing', sysdate, {TAB_TR_ID}, {f_id})'''
          c.execute(insert_query)
          conn.commit()

          #UPDATE INVENTORY
          inventory_query = f"UPDATE food SET f_inv = f_inv - {f_qty} WHERE f_id = {f_id}"
          c.execute(inventory_query)
          conn.commit()

          # -------------------- TO DO ----------------------
          # If F_INV[f_id] = SHOPPING_CART[f_id] --> update F_AVAIL to 'N'

        self.list_shopping_cart_vbox.close()

        # Reset food variables
        reset_food_inv_cat(clear_cart=True)
        self.initialize_thank_you_vbox()
        display(self.thank_you_vbox)
      submit_btn.on_click(on_submit_button_clicked)

      #EMPTY CART HANDLING
      if len(SHOPPING_CART) == 0:
        submit_btn.disabled = True #Disable the "Submit Order" button

      # -------------------------------------------------------------------------------------------------------

      # Pack all hboxes into a vertical box, display
      self.list_shopping_cart_vbox = widgets.VBox([i for i in hboxes])

      display(self.list_shopping_cart_vbox)

  def initialize_thank_you_vbox(self):
    msg_labels = Label("You have submitted your order. Please wait.")


    thanks_btn = widgets.Button(description="Back")
    def on_thanks_btn_clicked(b):
      self.thank_you_vbox.close()
      MenuScreen()
    thanks_btn.on_click(on_thanks_btn_clicked)

    self.thank_you_vbox = widgets.VBox([msg_labels, thanks_btn])



In [ ]:
ms = ShoppingCart()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Ordered items

c4 → Ivan
1.   Create a screen to show ordered items
2.   Add a button to navigate back to MenuScreen()





In [ ]:
class OrderedItemsScreen:
    def __init__(self):
        # self.menu_screen_callback = menu_screen_callback
        self.ordered_items_grid = widgets.GridBox(children=[],
                                                  layout=widgets.Layout(
                                                      grid_template_columns='auto auto',
                                                      # grid_gap='10px 10px'
                                                  ))
        self.refresh_ordered_items()
        self.back_button = widgets.Button(description='Back')
        self.back_button.on_click(self.on_back_button_click)
        display(widgets.VBox([self.ordered_items_grid, self.back_button]))

    def refresh_ordered_items(self):
        # Fetch ordered items for the current transaction from the database
        ordered_items = self.get_ordered_items_from_db()

        # Clear the current items
        self.ordered_items_grid.children = []

        # Create header
        header_food = widgets.Label(value='𝗙𝗼𝗼𝗱')
        header_quantity = widgets.Label(value='𝗤𝘂𝗮𝗻𝘁𝗶𝘁𝘆')
        self.ordered_items_grid.children += (header_food, header_quantity)

        # Add rows for items
        for item, qty in ordered_items:
            label_food = widgets.Label(value=item)
            label_qty = widgets.Label(value=str(qty))
            self.ordered_items_grid.children += (label_food, label_qty)

    def get_ordered_items_from_db(self):
        # This function queries the database and returns a list of tuples (item, quantity)
        global c, TAB_TR_ID
        ordered_items = []

        # Query to get the name and quantity of food items ordered in the current transaction
        query = """
        SELECT f.f_name, co.co_qty
        FROM cooking_order co
        JOIN food f ON co.food_f_id = f.f_id
        WHERE co.transaction_tr_id = :tr_id AND co.co_status != 'Paid'
        """
        c.execute(query, {'tr_id': TAB_TR_ID})
        ordered_items = c.fetchall()

        return ordered_items

    def on_back_button_click(self, b):
        self.ordered_items_grid.close()
        self.back_button.close()
        # This will navigate back to the MenuScreen.
        MenuScreen()

In [ ]:
TAB_TR_ID = 8

In [ ]:
OrderedItemsScreen()

## ResetTablet

In [ ]:
class ResetTablet:
  proceed_to_cashier_grid = None
  confirm_reset_vbox = None
  username = None
  password = None

  def __init__(self):
    self.initialize_proceed_to_cashier()

  def initialize_proceed_to_cashier(self):
    self.proceed_to_cashier_grid = GridspecLayout(5, 2,
                                             layout = widgets.Layout(justify_items = 'center'),
                                             width = '400px')

    proceed_to_cashier_label = Label(value = "Please proceed to the cashier with this tablet.")
    table_label = Label(value = "Table " + str(TAB_TA_ID))

    # ----------------------------------------------------------------------------------------------------------------

    # Button: Back
    back_btn = widgets.Button(description = 'Back')
    def on_back_btn_clicked(b):
      self.proceed_to_cashier_grid.close()
      MenuScreen()
    back_btn.on_click(on_back_btn_clicked)

    # ----------------------------------------------------------------------------------------------------------------

    # Button: Reset
    reset_btn = widgets.Button(description = 'Reset Tablet')
    def on_reset_btn_clicked(b):
      self.proceed_to_cashier_grid.close()
      self.initialize_confirm_reset()
    reset_btn.on_click(on_reset_btn_clicked)

    # ----------------------------------------------------------------------------------------------------------------

    # Display
    self.proceed_to_cashier_grid[0, :] = proceed_to_cashier_label
    self.proceed_to_cashier_grid[2, :] = table_label
    self.proceed_to_cashier_grid[4, :] = widgets.HBox([back_btn, reset_btn])

    display(self.proceed_to_cashier_grid)

    # ----------------------------------------------------------------------------------------------------------------

  def initialize_confirm_reset(self):
    login_to_reset_label = widgets.Label(value='𝗟𝗼𝗴𝗶𝗻 𝘁𝗼 𝗥𝗲𝘀𝗲𝘁')
    username_field = widgets.Text(description='Username:')
    password_field = widgets.Password(description='Password:')
    invalid_login_label = Label(value="Invalid username/password.")
    invalid_login_label.layout.visibility='hidden'

    # ----------------------------------------------------------------------------------------------------------------

    # Button: Confirm Reset
    reset_btn = widgets.Button(description='Confirm Reset')

    def on_reset_btn_clicked(_):
        self.username = username_field.value
        self.password = password_field.value

        # Check username and password
        if not check_password(self.username, self.password):
          invalid_login_label.layout.visibility = 'visible'
        else:
          global TAB_TA_ID
          global TAB_TR_ID
          c.execute(f"UPDATE tablee SET ta_status='Available' WHERE ta_id = {TAB_TA_ID}")
          c.execute("commit")

          # Reset the global variables
          reset_global_variables()

          # Close the confirm_reset screen
          self.confirm_reset_vbox.close()

          # Navigate to SelectTable screen
          SelectTable()

    reset_btn.on_click(on_reset_btn_clicked)

    # ----------------------------------------------------------------------------------------------------------------

    # Display
    self.confirm_reset_vbox = widgets.VBox([login_to_reset_label, username_field, password_field, invalid_login_label, reset_btn],
                                      layout = widgets.Layout(display='center', flex_flow='col', justify_content='center', align_items='center', width='400px'))
    display(self.confirm_reset_vbox)

# **Tablet - DEMO**

In [ ]:
ms = MenuScreen()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
tablet = SelectTable()